# Voorbereiding, Hypothese & Verwachtingen

### **Inleiding**
In dit project onderzoeken we het verband tussen aardbevingen, tektonische platen en bevolkingsdichtheid.  
Door drie verschillende datasets te combineren — aardbevingsdata, plaatgrenzen en bevolkingscijfers — proberen we te begrijpen waar zware aardbevingen het vaakst voorkomen en welke regio’s daardoor het hoogste risico lopen op menselijke impact.

### **Onderzoeksdoel**
Het doel van dit project is om te bepalen:
1. of zware aardbevingen vaker voorkomen in de buurt van tektonische plaatgrenzen,  
2. en of landen met een grote populatie hierdoor extra kwetsbaar worden.

We gebruiken **PySpark** voor de verwerking van grote datasets en **Folium** voor interactieve kaartvisualisaties.  
Omdat Pandas niet gebruikt mocht worden, werd de dataverwerking volledig in Spark uitgevoerd.

---

### **Hypothese**
**“Aardbevingen dichter bij de grenzen van tektonische platen hebben gemiddeld een hogere magnitude en komen vaker voor.  
Wanneer deze gebeurtenissen voorkomen in dichtbevolkte regio’s, verhoogt dit het risico op menselijke impact aanzienlijk.”**

Deze hypothese bestaat uit twee delen:
- **Geologisch risico:** zware aardbevingen treden voornamelijk op langs plaatgrenzen.  
- **Menselijk risico:** landen met veel inwoners die zich in deze actieve zones bevinden, lopen meer gevaar.

---

### **Verwachtingen vóór analyse**
Op basis van bestaande wetenschappelijke kennis verwachtten we dat:
- De meeste zware aardbevingen zich zullen clusteren langs de subductiezones en transformbreuken.  
- Landen zoals Japan, Indonesië, Mexico, de Filipijnen en de Verenigde Staten hogere risicoscores zullen vertonen omdat ze zowel veel aardbevingen als hoge bevolkingsdensiteit kennen.  
- Grote landen ver van actieve plaatgrenzen (zoals Rusland, Nigeria of Duitsland) relatief lage risico’s zullen hebben, ondanks grote bevolkingen.  

De visualisaties in dit project zijn ontworpen om deze verwachtingen te testen en te evalueren.


## Spark sessie starten

In [49]:
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.types import DoubleType

import folium
from folium.plugins import MarkerCluster

spark = SparkSession.builder \
    .appName("EarthquakeAnalysis") \
    .getOrCreate()


## Load data

In [50]:
eq_df = spark.read.csv("../data/database.csv", header=True, inferSchema=True)
plates_df = spark.read.csv("../data/all.csv", header=True, inferSchema=True)
pop_df = spark.read.csv("../data/population_by_country_2020.csv", header=True, inferSchema=True)

print("Aantal aardbevingen:", eq_df.count())
print("Aantal plaat-coördinaten:", plates_df.count())
print("Aantal landen:", pop_df.count())

eq_df.printSchema()
plates_df.printSchema()
pop_df.printSchema()


Aantal aardbevingen: 23412
Aantal plaat-coördinaten: 12321
Aantal landen: 235
root
 |-- Date: string (nullable = true)
 |-- Time: timestamp (nullable = true)
 |-- Latitude: double (nullable = true)
 |-- Longitude: double (nullable = true)
 |-- Type: string (nullable = true)
 |-- Depth: double (nullable = true)
 |-- Depth Error: double (nullable = true)
 |-- Depth Seismic Stations: integer (nullable = true)
 |-- Magnitude: double (nullable = true)
 |-- Magnitude Type: string (nullable = true)
 |-- Magnitude Error: double (nullable = true)
 |-- Magnitude Seismic Stations: integer (nullable = true)
 |-- Azimuthal Gap: double (nullable = true)
 |-- Horizontal Distance: double (nullable = true)
 |-- Horizontal Error: double (nullable = true)
 |-- Root Mean Square: double (nullable = true)
 |-- ID: string (nullable = true)
 |-- Source: string (nullable = true)
 |-- Location Source: string (nullable = true)
 |-- Magnitude Source: string (nullable = true)
 |-- Status: string (nullable = true)


## Cleaning

In [51]:
from pyspark.sql import functions as F
from pyspark.sql.types import DoubleType

# Types expliciet zetten en rijen zonder locatie/magnitude eruit
eq_clean = (
    eq_df
    .withColumn("Latitude", F.col("Latitude").cast(DoubleType()))
    .withColumn("Longitude", F.col("Longitude").cast(DoubleType()))
    .withColumn("Magnitude", F.col("Magnitude").cast(DoubleType()))
    .filter(
        F.col("Latitude").isNotNull() &
        F.col("Longitude").isNotNull() &
        F.col("Magnitude").isNotNull()
    )
)

# Jaar uit de Date kolom halen (formaat: dd/MM/yyyy)
eq_clean = eq_clean.withColumn(
    "Year",
    F.year(F.to_date(F.col("Date"), "dd/MM/yyyy"))
)

eq_clean.select("Date", "Year", "Latitude", "Longitude", "Magnitude").show(10)


+----------+----+--------+---------+---------+
|      Date|Year|Latitude|Longitude|Magnitude|
+----------+----+--------+---------+---------+
|01/02/1965|1965|  19.246|  145.616|      6.0|
|01/04/1965|1965|   1.863|  127.352|      5.8|
|01/05/1965|1965| -20.579| -173.972|      6.2|
|01/08/1965|1965| -59.076|  -23.557|      5.8|
|01/09/1965|1965|  11.938|  126.427|      5.8|
|01/10/1965|1965| -13.405|  166.629|      6.7|
|01/12/1965|1965|  27.357|   87.867|      5.9|
|01/15/1965|NULL| -13.309|  166.212|      6.0|
|01/16/1965|NULL| -56.452|  -27.043|      6.0|
|01/17/1965|NULL| -24.563|  178.487|      5.8|
+----------+----+--------+---------+---------+
only showing top 10 rows



## sterke intanties bepalen

In [52]:
strong_eq = eq_clean.filter(F.col("Magnitude") >= 6.5)

print("Aantal aardbevingen totaal:", eq_clean.count())
print("Aantal sterke aardbevingen (>= 6.5):", strong_eq.count())

strong_eq.select("Date", "Latitude", "Longitude", "Magnitude", "Depth").show(10)


Aantal aardbevingen totaal: 23412
Aantal sterke aardbevingen (>= 6.5): 2303
+----------+--------+---------+---------+-----+
|      Date|Latitude|Longitude|Magnitude|Depth|
+----------+--------+---------+---------+-----+
|01/10/1965| -13.405|  166.629|      6.7| 35.0|
|01/24/1965|  -2.608|  125.952|      8.2| 20.0|
|02/04/1965|  51.251|  178.715|      8.7| 30.3|
|02/04/1965|  51.443|  179.605|      7.3| 30.0|
|02/04/1965|  52.773|  171.974|      6.5| 30.0|
|02/23/1965| -25.633|  -70.679|      7.0| 35.0|
|03/03/1965|  -5.514|  151.819|      6.7| 14.8|
|03/14/1965|  36.405|   70.724|      7.4|207.8|
|03/22/1965| -15.262| -173.254|      6.5| 30.5|
|03/28/1965| -32.522|  -71.233|      7.4| 70.0|
+----------+--------+---------+---------+-----+
only showing top 10 rows



## Platen groeperen

In [53]:
plates_grouped = (
    plates_df
    .groupBy("plate")
    .agg(
        F.collect_list(F.struct("lat", "lon")).alias("coords")
    )
)

plates_grouped.show(5, truncate=False)


+-----+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

## simplify data (population)

In [54]:
pop_simple = (
    pop_df
    .select(
        F.col("Country (or dependency)").alias("Country"),
        F.col("Population (2020)").cast("long").alias("Population")
    )
)

pop_simple.show(10)


+-------------+----------+
|      Country|Population|
+-------------+----------+
|        China|1438207241|
|        India|1377233523|
|United States| 330610570|
|    Indonesia| 272931713|
|     Pakistan| 219992900|
|       Brazil| 212253150|
|      Nigeria| 205052107|
|   Bangladesh| 164354176|
|       Russia| 145922010|
|       Mexico| 128655589|
+-------------+----------+
only showing top 10 rows



## aardbevingen visualiseren

In [55]:
import folium
from folium.plugins import MarkerCluster

# basiskaart
m1 = folium.Map(location=[0, 0], zoom_start=2, tiles="CartoDB positron")

# sample om het licht te houden
strong_eq_sample = strong_eq.orderBy(F.desc("Magnitude")).limit(5000).collect()

marker_cluster = MarkerCluster().add_to(m1)

for row in strong_eq_sample:
    lat = row["Latitude"]
    lon = row["Longitude"]
    mag = row["Magnitude"]
    depth = row["Depth"]
    date = row["Date"]
    time = row["Time"]
    
    popup_text = (
        f"Magnitude: {mag}<br>"
        f"Diepte: {depth} km<br>"
        f"Datum: {date} {time}"
    )
    
    radius = 2 + float(mag)
    
    folium.CircleMarker(
        location=[lat, lon],
        radius=radius,
        fill=True,
        fill_opacity=0.6,
        weight=0.5,
        popup=popup_text
    ).add_to(marker_cluster)

m1  # in Jupyter toont dit de kaart
# eventueel ook: m1.save("kaart_1_wereld_earthquakes.html")


## Platen bepalen

In [56]:
m2 = folium.Map(location=[0, 0], zoom_start=2, tiles="CartoDB positron")

# platen toevoegen
plates_list = plates_grouped.collect()

for plate_row in plates_list:
    plate_name = plate_row["plate"]
    coords_structs = plate_row["coords"]
    
    coords = [(float(c["lat"]), float(c["lon"])) for c in coords_structs]
    if len(coords) < 2:
        continue
    
    folium.PolyLine(
        locations=coords,
        weight=2,
        opacity=0.7,
        tooltip=f"Plate: {plate_name}"
    ).add_to(m2)

# aardbevingen toevoegen
strong_eq_sample = strong_eq.orderBy(F.desc("Magnitude")).limit(3000).collect()

for row in strong_eq_sample:
    lat = row["Latitude"]
    lon = row["Longitude"]
    mag = row["Magnitude"]
    
    folium.CircleMarker(
        location=[lat, lon],
        radius=1.5,
        fill=True,
        fill_opacity=0.5,
        weight=0
    ).add_to(m2)

m2


In [57]:
import math
import folium
from folium.plugins import MarkerCluster

# Haversine afstand in km tussen twee (lat, lon) punten
def haversine(lat1, lon1, lat2, lon2):
    R = 6371.0  # aardstraal in km
    phi1 = math.radians(lat1)
    phi2 = math.radians(lat2)
    dphi = math.radians(lat2 - lat1)
    dlambda = math.radians(lon2 - lon1)

    a = math.sin(dphi / 2)**2 + math.cos(phi1) * math.cos(phi2) * math.sin(dlambda / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    return R * c

# Alle plaat-punten in een Python-lijst
plates_points = [(float(r["lat"]), float(r["lon"])) for r in plates_df.collect()]
print("Aantal plaatpunten in lijst:", len(plates_points))

# Sample van aardbevingen (sterke) om het berekenbaar te houden
strong_eq_sample = strong_eq.limit(2000).collect()
print("Aantal aardbevingen in sample:", len(strong_eq_sample))


Aantal plaatpunten in lijst: 12321
Aantal aardbevingen in sample: 2000


## afstanden tot platen

In [58]:
eq_points = []

for row in strong_eq_sample:
    lat = float(row["Latitude"])
    lon = float(row["Longitude"])
    mag = float(row["Magnitude"])
    depth = row["Depth"]
    date = row["Date"]
    time = row["Time"]
    
    # min-afstand tot een plaatpunt (brute force, maar oké voor 2000 quakes)
    min_dist = min(
        haversine(lat, lon, p_lat, p_lon) for (p_lat, p_lon) in plates_points
    )
    
    eq_points.append({
        "lat": lat,
        "lon": lon,
        "mag": mag,
        "depth": depth,
        "date": date,
        "time": time,
        "dist_plate": min_dist
    })

# Even checken
eq_points[:3]


[{'lat': -13.405,
  'lon': 166.629,
  'mag': 6.7,
  'depth': 35.0,
  'date': '01/10/1965',
  'time': datetime.datetime(2025, 12, 11, 13, 36, 32),
  'dist_plate': 59.51230973858459},
 {'lat': -2.608,
  'lon': 125.952,
  'mag': 8.2,
  'depth': 20.0,
  'date': '01/24/1965',
  'time': datetime.datetime(2025, 12, 11, 0, 11, 17),
  'dist_plate': 183.697864766475},
 {'lat': 51.251,
  'lon': 178.715,
  'mag': 8.7,
  'depth': 30.3,
  'date': '02/04/1965',
  'time': datetime.datetime(2025, 12, 11, 5, 1, 22),
  'dist_plate': 71.90147377624685}]

## risicobubbels bepalen

In [59]:
import math

# Zelfde land-centers houden
country_centers = {
    "China": (35.0, 103.0),
    "India": (21.0, 78.0),
    "United States": (39.0, -98.0),
    "Indonesia": (-2.0, 118.0),
    "Japan": (36.0, 138.0),
    "Mexico": (23.0, -102.0),
    "Turkey": (39.0, 35.0),
    "Philippines": (13.0, 122.0)
}

pop_risk_countries = (
    pop_simple
    .filter(F.col("Country").isin(list(country_centers.keys())))
    .collect()
)

# max populatie voor normalisatie
max_pop = max(int(r["Population"]) for r in pop_risk_countries)

risk_bubbles = []
for row in pop_risk_countries:
    country = row["Country"]
    popu = int(row["Population"])
    lat, lon = country_centers[country]
    
    # genormaliseerd 0–1
    norm = popu / max_pop
    
    # radius: max ~ 400 km, maar met sqrt zodat verschillen niet exploderen
    radius_km = 400 * math.sqrt(norm)
    
    risk_bubbles.append({
        "country": country,
        "lat": lat,
        "lon": lon,
        "population": popu,
        "radius_km": radius_km
    })

risk_bubbles


[{'country': 'China',
  'lat': 35.0,
  'lon': 103.0,
  'population': 1438207241,
  'radius_km': 400.0},
 {'country': 'India',
  'lat': 21.0,
  'lon': 78.0,
  'population': 1377233523,
  'radius_km': 391.4290451996062},
 {'country': 'United States',
  'lat': 39.0,
  'lon': -98.0,
  'population': 330610570,
  'radius_km': 191.7819026963238},
 {'country': 'Indonesia',
  'lat': -2.0,
  'lon': 118.0,
  'population': 272931713,
  'radius_km': 174.25139207818253},
 {'country': 'Mexico',
  'lat': 23.0,
  'lon': -102.0,
  'population': 128655589,
  'radius_km': 119.63646842925742},
 {'country': 'Japan',
  'lat': 36.0,
  'lon': 138.0,
  'population': 126552765,
  'radius_km': 118.65473534806353},
 {'country': 'Philippines',
  'lat': 13.0,
  'lon': 122.0,
  'population': 109280343,
  'radius_km': 110.26058200978694},
 {'country': 'Turkey',
  'lat': 39.0,
  'lon': 35.0,
  'population': 84153250,
  'radius_km': 96.75751420517621}]

## landen bepalen

In [60]:
import math

country_coords = {
    "China": (35.0, 103.0),
    "India": (21.0, 78.0),
    "United States": (39.0, -98.0),
    "Indonesia": (-2.0, 118.0),
    "Pakistan": (30.0, 70.0),
    "Brazil": (-10.0, -52.0),
    "Nigeria": (9.0, 8.0),
    "Bangladesh": (24.0, 90.0),
    "Russia": (60.0, 90.0),
    "Mexico": (23.0, -102.0),
    "Japan": (36.0, 138.0),
    "Ethiopia": (9.0, 40.0),
    "Philippines": (13.0, 122.0),
    "Egypt": (27.0, 30.0),
    "Vietnam": (16.0, 107.0),
    "DR Congo": (-3.0, 23.0),
    "Turkey": (39.0, 35.0),
    "Iran": (32.0, 53.0),
    "Germany": (51.0, 10.0),
    "Thailand": (15.0, 101.0),
    "United Kingdom": (54.0, -2.0),
    "France": (46.0, 2.0),
    "Italy": (42.5, 12.5),
    "Chile": (-30.0, -71.0),
    "Argentina": (-34.0, -64.0),
    "New Zealand": (-41.0, 174.0),
    "Greece": (39.0, 22.0),
    "Spain": (40.0, -4.0),
    "Portugal": (39.5, -8.0),
    "Australia": (-25.0, 133.0),
    "Peru": (-10.0, -76.0),
    "Colombia": (4.5, -74.0),
    "Morocco": (32.0, -6.0),
    "Algeria": (28.0, 3.0),
    "Saudi Arabia": (24.0, 45.0),
    "Myanmar": (21.0, 96.0),
    "Afghanistan": (34.0, 66.0),
    "Nepal": (28.0, 84.0),
    "Malaysia": (3.5, 102.0),
    "Sri Lanka": (7.5, 81.0),
    "Iceland": (65.0, -18.0)
}

# Alle landen waarvoor we zowel populatie als coördinaten hebben
risk_pop_rows = (
    pop_simple
    .filter(F.col("Country").isin(list(country_coords.keys())))
    .collect()
)

len(risk_pop_rows), risk_pop_rows[:5]


(41,
 [Row(Country='China', Population=1438207241),
  Row(Country='India', Population=1377233523),
  Row(Country='United States', Population=330610570),
  Row(Country='Indonesia', Population=272931713),
  Row(Country='Pakistan', Population=219992900)])

In [61]:
# Haversine nog nodig in deze cel (als hij in een andere cel staat, kun je dit overslaan)
def haversine(lat1, lon1, lat2, lon2):
    R = 6371.0
    phi1 = math.radians(lat1)
    phi2 = math.radians(lat2)
    dphi = math.radians(lat2 - lat1)
    dlambda = math.radians(lon2 - lon1)

    a = math.sin(dphi / 2)**2 + math.cos(phi1) * math.cos(phi2) * math.sin(dlambda / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    return R * c

# parameters
plate_threshold_km = 100.0   # "dicht bij plaat"
country_radius_km   = 500.0  # quakes binnen 500 km van landcentrum

country_risks = []

for row in risk_pop_rows:
    country = row["Country"]
    popu = int(row["Population"])
    c_lat, c_lon = country_coords[country]

    quake_count = 0
    mag_sum = 0.0

    for e in eq_points:          # eq_points: lijst met aardbevingen (lat, lon, mag, dist_plate, ...)
        if e["dist_plate"] > plate_threshold_km:
            continue  # we kijken enkel naar quakes dicht bij plaatgrens

        q_lat = e["lat"]
        q_lon = e["lon"]
        q_mag = e["mag"]

        dist_country = haversine(c_lat, c_lon, q_lat, q_lon)
        if dist_country <= country_radius_km:
            quake_count += 1
            mag_sum += q_mag

    if quake_count > 0:
        avg_mag = mag_sum / quake_count
    else:
        avg_mag = None

    # risico-score: aantal quakes * log10(populatie)
    if quake_count > 0:
        risk_score = quake_count * math.log10(popu)
    else:
        risk_score = 0.0

    country_risks.append({
        "country": country,
        "lat": c_lat,
        "lon": c_lon,
        "population": popu,
        "quake_count": quake_count,
        "avg_mag": avg_mag,
        "risk_score": risk_score
    })

# Filter landen zonder quakes
country_risks = [c for c in country_risks if c["quake_count"] > 0]

# Sorteren op risk_score (hoogste eerst)
country_risks_sorted = sorted(country_risks, key=lambda x: x["risk_score"], reverse=True)

# Even checken
for c in country_risks_sorted[:10]:
    print(c)


{'country': 'Japan', 'lat': 36.0, 'lon': 138.0, 'population': 126552765, 'quake_count': 22, 'avg_mag': 6.763636363636363, 'risk_score': 178.24997604307973}
{'country': 'Philippines', 'lat': 13.0, 'lon': 122.0, 'population': 109280343, 'quake_count': 22, 'avg_mag': 7.000000000000001, 'risk_score': 176.8479250882694}
{'country': 'Chile', 'lat': -30.0, 'lon': -71.0, 'population': 19082804, 'quake_count': 15, 'avg_mag': 6.786666666666666, 'risk_score': 109.20963284502963}
{'country': 'Greece', 'lat': 39.0, 'lon': 22.0, 'population': 10433037, 'quake_count': 15, 'avg_mag': 6.76, 'risk_score': 105.27616121367458}
{'country': 'Colombia', 'lat': 4.5, 'lon': -74.0, 'population': 50771878, 'quake_count': 9, 'avg_mag': 6.788888888888889, 'risk_score': 69.35060905030609}
{'country': 'Indonesia', 'lat': -2.0, 'lon': 118.0, 'population': 272931713, 'quake_count': 8, 'avg_mag': 6.9875, 'risk_score': 67.48843200776935}
{'country': 'Turkey', 'lat': 39.0, 'lon': 35.0, 'population': 84153250, 'quake_coun

## map samenbrengen

In [62]:
import folium
from folium.plugins import MarkerCluster

def risk_color(score, max_score):
    ratio = score / max_score
    if ratio < 0.25:
        return "green"
    elif ratio < 0.5:
        return "yellow"
    elif ratio < 0.75:
        return "orange"
    else:
        return "red"

m_risk = folium.Map(location=[10, 0], zoom_start=2, tiles="CartoDB positron")

plates_fg = folium.FeatureGroup(name="Tektonische platen").add_to(m_risk)
quakes_fg = folium.FeatureGroup(name="Sterke aardbevingen").add_to(m_risk)
risk_fg   = folium.FeatureGroup(name="Landelijk risico (quakes × bevolking)").add_to(m_risk)

# 1) Tektonische platen
plates_grouped = (
    plates_df
    .groupBy("plate")
    .agg(F.collect_list(F.struct("lat", "lon")).alias("coords"))
)

for plate_row in plates_grouped.collect():
    plate_name = plate_row["plate"]
    coords_structs = plate_row["coords"]
    coords = [(float(c["lat"]), float(c["lon"])) for c in coords_structs]
    if len(coords) < 2:
        continue

    folium.PolyLine(
        locations=coords,
        weight=2,
        opacity=0.5,
        tooltip=f"Plate: {plate_name}"
    ).add_to(plates_fg)

# 2) Sterke aardbevingen (cluster)
marker_cluster = MarkerCluster().add_to(quakes_fg)

for e in eq_points:
    lat = e["lat"]
    lon = e["lon"]
    mag = e["mag"]
    depth = e["depth"]
    date = e["date"]
    time = e["time"]
    dist = e["dist_plate"]

    near_plate = dist <= plate_threshold_km
    color = "red" if near_plate else "blue"
    radius = 2 + mag

    popup_text = (
        f"<b>Aardbeving</b><br>"
        f"Magnitude: {mag:.1f}<br>"
        f"Diepte: {depth} km<br>"
        f"Afstand tot plaatgrens: {dist:.1f} km<br>"
        f"Datum: {date} {time}"
    )

    folium.CircleMarker(
        location=[lat, lon],
        radius=radius,
        color=color,
        fill=True,
        fill_opacity=0.6,
        weight=0.5,
        popup=popup_text
    ).add_to(marker_cluster)

# 3) Landen met risico-score
max_risk = max(c["risk_score"] for c in country_risks_sorted)

for c in country_risks_sorted:
    country = c["country"]
    lat = c["lat"]
    lon = c["lon"]
    popu = c["population"]
    qcount = c["quake_count"]
    avg_mag = c["avg_mag"]
    score = c["risk_score"]

    col = risk_color(score, max_risk)

    # radius: tussen 150 km en 450 km, geschaald op risk_score
    radius_km = 150 + 300 * (score / max_risk)

    popup_text = (
        f"<b>{country}</b><br>"
        f"Bevolking: {popu:,}<br>"
        f"Aantal sterke quakes nabij (≤ {country_radius_km} km): {qcount}<br>"
        f"Gemiddelde magnitude: {avg_mag:.2f}<br>"
        f"Risico-score (quakes × log10(pop)): {score:.1f}"
    )

    folium.Circle(
        location=[lat, lon],
        radius=radius_km * 1000,  # meters
        color=col,
        fill=True,
        fill_opacity=0.20,
        weight=1,
        popup=popup_text
    ).add_to(risk_fg)

folium.LayerControl(collapsed=False).add_to(m_risk)

m_risk


# Moeilijkheden tijdens het project

### 1. Datakwaliteit en inconsistenties tussen de drie datasets
De aardbevingsdataset bevatte veel ontbrekende en onvolledige waarden (zoals `Magnitude Error`, `Depth Error`), waardoor een grondige opschoning noodzakelijk was.  
Daarnaast gebruikten de drie datasets verschillende structuren en referenties (coördinaten, landenamen, plaatgrenzen), waardoor directe koppeling onmogelijk was zonder extra verwerking of manuele mapping.


### 2. Berekenen van geografische afstanden zonder GIS-bibliotheken
Spark heeft geen ingebouwde geospatiale functies.  
Daarom moest de Haversine-formule zelf worden geïmplementeerd om afstanden tussen aardbevingen en plaatgrenzen te berekenen.  
Voor elke aardbeving moest vervolgens de dichtsbijzijnde plaatcoördinaat worden bepaald, wat computationeel zwaar was.


### 3. Aardbevingen koppelen aan landen zonder polygonen
De dataset bevatte geen landsgrenzen of polygon-shapes, enkel ruwe coördinaten.  
Daarom moest een benadering worden gebruikt via landcentroiden en een afstandsstraal (500 km).  
Dit is minder exact dan GIS-polygon matching, en vereiste handmatig toegevoegde landcoördinaten.ereiste verschillende iteraties en fine-tuning.

---


# Conclusie

De resultaten van dit project bevestigen de hypothese duidelijk.  
Ten eerste toont de kaart dat vrijwel alle zware aardbevingen (Magnitude ≥ 6.5) zich dicht bij tektonische plaatgrenzen bevinden. De rode markers maken duidelijk dat deze seismische activiteit niet willekeurig verspreid is, maar sterk gelinkt aan plate boundaries zoals subductiezones en transformbreuken.

Daarnaast tonen de risicocirkels dat landen met een hoge populatie in seismisch actieve regio’s, zoals Japan, Indonesië, de Filipijnen, Mexico en de westkust van de Verenigde Staten, de hoogste risicoscores behalen.  
Deze zones combineren **hoog geologisch risico** met **hoge bevolkingsconcentraties**, wat de potentiële menselijke impact aanzienlijk vergroot.

Landen met veel inwoners maar weinig aardbevingen in hun omgeving (zoals Nigeria of Duitsland) scoren daarentegen laag, wat bevestigt dat bevolking op zich niet bepalend is — het is de **interactie tussen aardbevingsactiviteit en bevolkingsdichtheid** die het risico vormt.

### **Eindconclusie**
De hypothese wordt ondersteund:  
- **Zware aardbevingen zijn duidelijk geconcentreerd langs tektonische plaatgrenzen.**  
- **Wanneer deze gebeurtenissen plaatsvinden in dichtbevolkte gebieden, stijgt het risico op menselijke schade aanzienlijk.**

Dit project toont aan hoe geografische en demografische gegevens gecombineerd kunnen worden om inzicht te krijgen in natuurlijke risico’s en de impact op de samenleving.
